## Import & Setup

Note, if you are getting errors like this:
```
...
from .extension import *
  File ".../isaacsim/extsUser/go4robo/go4robo_python/extension.py", line 3, in <module>
    import omni.ext
ModuleNotFoundError: No module named 'omni'
```

Go into `isaacsim/extsUser/go4robo/go4robo_python/__init__.py` and comment out the following line:
```
from .extension import *
```

!! You need to uncomment this line if you plan to run the Isaac Sim extension !!

In [4]:
#Enable reloading because restarting the kernel is a pain
%load_ext autoreload
%autoreload 2

%pip install -q usd-core

import matplotlib.pyplot as plt
import matplotlib.animation as animation
from IPython.display import HTML

import numpy as np

from isaacsim.extsUser.go4robo.go4robo_python import bot_3d_problem as g4r_problem
from isaacsim.extsUser.go4robo.go4robo_python import bot_3d_rep as g4r_rep

import json

import os, sys

import copy

from jupyter_dash import JupyterDash
from dash import html, dcc, Input, Output
import plotly.graph_objects as go
import pandas as pd

from tqdm.notebook import trange, tqdm

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
Note: you may need to restart the kernel to use updated packages.


## Get the generated designs from csv

In [2]:
df_csv_path = "/Users/robosquiggles/Downloads/designs_Robot_20250502_041014.csv" # This should also contain the prior design at index 0

df = pd.read_csv(df_csv_path)
df

id          Name  Cost  Perception Entropy  Generation  s0_type  \
0          0  Prior Design   4.0            3.117923           0        1   
1          1      Design 1   2.0            3.697159           1        1   
2          2      Design 2   2.0            3.624025           1        1   
3          3      Design 3   4.0            3.205183           1        1   
4          4      Design 4   4.0            3.152721           1        1   
...      ...           ...   ...                 ...         ...      ...   
34996  34996  Design 34996   4.0            2.404299         500        1   
34997  34997  Design 34997   2.0            2.742909         500        1   
34998  34998  Design 34998   6.0            2.208865         500        1   
34999  34999  Design 34999   8.0            2.069230         500        1   
35000  35000  Design 35000   8.0            2.069230         500        1   

           s0_x      s0_y      s0_z         s0_qw  ...     s3_qy     s3_qz  \
0      0.000000  0.000000  0.500000  6.123234e-17  ...  0.000000  0.000000   
1      0.770239  0.731729  0.259698  7.773285e-02  ...  0.000000  0.000000   
2      0.636604  0.993913  0.546071 -4.580510e-01  ...  0.000000  0.000000   
3      0.441904  0.581577  0.989752  2.033107e-01  ...  0.000000  0.000000   
4      0.843840  0.381016  0.749858 -1.190455e-01  ...  0.000000  0.000000   
...         ...       ...       ...           ...  ...       ...       ...   
34996  0.191860  0.125378  0.999996  5.794378e-01  ...  0.000000  0.000000   
34997  0.090174  0.282961  0.999996  1.734295e-01  ...  0.000000  0.000000   
34998  0.380414  0.028790  0.999987  5.751684e-01  ...  0.000000  0.000000   
34999  0.491060  0.002016  0.999816  5.952870e-01  ... -0.588636  0.054839   
35000  0.491060  0.002016  0.999816  5.952870e-01  ... -0.588636  0.054839   

       s4_type  s4_x  s4_y  s4_z  s4_qw  s4_qx  s4_qy  s4_qz  
0            0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
1            0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
2            0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
3            0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
4            0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
...        ...   ...   ...   ...    ...    ...    ...    ...  
34996        0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
34997        0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
34998        0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
34999        0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  
35000        0   0.0   0.0   0.0    0.0    0.0    0.0    0.0  

[35001 rows x 45 columns]

## Plot the tradespace

Conveniently you can do this without the Problem definition, assuming you used the standard problem definition.

In [21]:
g4r_problem.plot_tradespace(df)

## Set up the problem from json

In [5]:
json_prolem_path = "/Users/robosquiggles/Downloads/problem_Robot_20250502_090557.json" # This will contain the prior design at problem.prior_bot

problem_json_dict = json.load(open(json_prolem_path, 'r'))

problem = g4r_problem.SensorPkgOptimization.from_json(problem_json_dict)

prior_bot_from_problem = problem.prior_bot

## Plot any bot from the df above

In [ ]:
INDEX_TO_PLOT = 28769

design_dict = df[df["id"] == INDEX_TO_PLOT].iloc[0].to_dict()
bot = problem.convert_1D_to_bot(design_dict)
bot.plot_bot_3d(
    perception_space=problem.perception_space,
    show=False,
    width=600,
)